# Deep Reinforcement Learning using AlphaZero methodology

Please see https://applied-data.science/blog/how-to-build-your-own-alphazero-ai-using-python-and-keras/ for further notes on the codebase

## 1. First load the core libraries

In [2]:
# -*- coding: utf-8 -*-
# %matplotlib inline

import numpy as np
np.set_printoptions(suppress=True)

from shutil import copyfile
import random

from tensorflow.python.keras.utils.vis_utils import plot_model
#from keras.utils import plot_model

from game import Game, GameState
from agent import Agent
from memory import Memory
from model import Residual_CNN
from funcs import playMatches, playMatchesBetweenVersions

import loggers as lg

from settings import run_folder, run_archive_folder
import initialise
import pickle

import os
os.environ["PATH"] += os.pathsep + 'C:/Users/RUSHI/Anaconda/'
os.environ["PATH"] += os.pathsep + 'C:/Program Files (x86)/graphviz-2.38/release/bin/'

import tensorflow as tf
import keras.backend.tensorflow_backend as tfback

print("tf.__version__ is", tf.__version__)
print("tf.keras.__version__ is:", tf.keras.__version__)

def _get_available_gpus():
    """Get a list of available gpu devices (formatted as strings).

    # Returns
        A list of available GPU devices.
    """
    #global _LOCAL_DEVICES
    if tfback._LOCAL_DEVICES is None:
        devices = tf.config.list_logical_devices()
        tfback._LOCAL_DEVICES = [x.name for x in devices]
    return [x for x in tfback._LOCAL_DEVICES if 'device:gpu' in x.lower()]

tfback._get_available_gpus = _get_available_gpus

tf.__version__ is 2.2.0
tf.keras.__version__ is: 2.3.0-tf


## 2. Now run this block to start the learning process

This block loops for ever, continually learning from new game data.

The current best model and memories are saved in the run folder so you can kill the process and restart from the last checkpoint.

In [5]:
lg.logger_main.info('=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*')
lg.logger_main.info('=*=*=*=*=*=.      NEW LOG      =*=*=*=*=*')
lg.logger_main.info('=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*')

env = Game()

# If loading an existing neural network, copy the config file to root
if initialise.INITIAL_RUN_NUMBER != None:
    copyfile(run_archive_folder + env.name + '/run' + str(initialise.INITIAL_RUN_NUMBER).zfill(4) + '/config.py', './config.py')

import config

######## LOAD MEMORIES IF NECESSARY ########

if initialise.INITIAL_MEMORY_VERSION == None:
    memory = Memory(config.MEMORY_SIZE)
else:
    print('LOADING MEMORY VERSION ' + str(initialise.INITIAL_MEMORY_VERSION) + '...')
    memory = pickle.load( open( run_archive_folder + env.name + '/run' + str(initialise.INITIAL_RUN_NUMBER).zfill(4) + "/memory/memory" + str(initialise.INITIAL_MEMORY_VERSION).zfill(4) + ".p",   "rb" ) )

######## LOAD MODEL IF NECESSARY ########

# create an untrained neural network objects from the config file
current_NN = Residual_CNN(config.REG_CONST, config.LEARNING_RATE, (2,) + env.grid_shape,   env.action_size, config.HIDDEN_CNN_LAYERS)
best_NN = Residual_CNN(config.REG_CONST, config.LEARNING_RATE, (2,) +  env.grid_shape,   env.action_size, config.HIDDEN_CNN_LAYERS)

#If loading an existing neural netwrok, set the weights from that model
if initialise.INITIAL_MODEL_VERSION != None:
    best_player_version  = initialise.INITIAL_MODEL_VERSION
    print('LOADING MODEL VERSION ' + str(initialise.INITIAL_MODEL_VERSION) + '...')
    m_tmp = best_NN.read(env.name, initialise.INITIAL_RUN_NUMBER, best_player_version)
    current_NN.model.set_weights(m_tmp.get_weights())
    best_NN.model.set_weights(m_tmp.get_weights())
#otherwise just ensure the weights on the two players are the same
else:
    best_player_version = 0
    best_NN.model.set_weights(current_NN.model.get_weights())

#copy the config file to the run folder
copyfile('./config.py', run_folder + 'config.py')
plot_model(current_NN.model, to_file=run_folder + 'models/model.png', show_shapes = True)

print('\n')

######## CREATE THE PLAYERS ########

current_player = Agent('current_player', env.state_size, env.action_size, config.MCTS_SIMS, config.CPUCT, current_NN)
best_player = Agent('best_player', env.state_size, env.action_size, config.MCTS_SIMS, config.CPUCT, best_NN)
#user_player = User('player1', env.state_size, env.action_size)
iteration = 0

while 1:

    iteration += 1
    #reload(lg)
    #reload(config)
    
    print('ITERATION NUMBER ' + str(iteration))
    
    lg.logger_main.info('BEST PLAYER VERSION: %d', best_player_version)
    print('BEST PLAYER VERSION ' + str(best_player_version))

    ######## SELF PLAY ########
    print('SELF PLAYING ' + str(config.EPISODES) + ' EPISODES...')
    _, memory, _, _ = playMatches(best_player, best_player, config.EPISODES, lg.logger_main, turns_until_tau0 = config.TURNS_UNTIL_TAU0, memory = memory)
    print('\n')
    
    memory.clear_stmemory()
    
    if len(memory.ltmemory) >= config.MEMORY_SIZE:

        ######## RETRAINING ########
        print('RETRAINING...')
        current_player.replay(memory.ltmemory)
        print('')

        if iteration % 5 == 0:
            pickle.dump( memory, open( run_folder + "memory/memory" + str(iteration).zfill(4) + ".p", "wb" ) )

        lg.logger_memory.info('====================')
        lg.logger_memory.info('NEW MEMORIES')
        lg.logger_memory.info('====================')
        
        memory_samp = random.sample(memory.ltmemory, min(1000, len(memory.ltmemory)))
        
        for s in memory_samp:
            current_value, current_probs, _ = current_player.get_preds(s['state'])
            best_value, best_probs, _ = best_player.get_preds(s['state'])

            lg.logger_memory.info('MCTS VALUE FOR %s: %f', s['playerTurn'], s['value'])
            lg.logger_memory.info('CUR PRED VALUE FOR %s: %f', s['playerTurn'], current_value)
            lg.logger_memory.info('BES PRED VALUE FOR %s: %f', s['playerTurn'], best_value)
            lg.logger_memory.info('THE MCTS ACTION VALUES: %s', ['%.2f' % elem for elem in s['AV']]  )
            lg.logger_memory.info('CUR PRED ACTION VALUES: %s', ['%.2f' % elem for elem in  current_probs])
            lg.logger_memory.info('BES PRED ACTION VALUES: %s', ['%.2f' % elem for elem in  best_probs])
            lg.logger_memory.info('ID: %s', s['state'].id)
            lg.logger_memory.info('INPUT TO MODEL: %s', current_player.model.convertToModelInput(s['state']))

            s['state'].render(lg.logger_memory)
            
        ######## TOURNAMENT ########
        print('TOURNAMENT...')
        scores, _, points, sp_scores = playMatches(best_player, current_player, config.EVAL_EPISODES, lg.logger_tourney, turns_until_tau0 = 0, memory = None)
        print('\nSCORES')
        print(scores)
        print('\nSTARTING PLAYER / NON-STARTING PLAYER SCORES')
        print(sp_scores)
        #print(points)

        print('\n\n')

        if scores['current_player'] > scores['best_player'] * config.SCORING_THRESHOLD:
            best_player_version = best_player_version + 1
            best_NN.model.set_weights(current_NN.model.get_weights())
            best_NN.write(env.name, best_player_version)

    else:
        print('MEMORY SIZE: ' + str(len(memory.ltmemory)))

I0621 03:14:26.269047  4576 <ipython-input-5-39ccd97d46fc>:1] =*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*
I0621 03:14:26.270045  4576 <ipython-input-5-39ccd97d46fc>:2] =*=*=*=*=*=.      NEW LOG      =*=*=*=*=*
I0621 03:14:26.271044  4576 <ipython-input-5-39ccd97d46fc>:3] =*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*
I0621 03:14:29.018571  4576 <ipython-input-5-39ccd97d46fc>:60] BEST PLAYER VERSION: 0
I0621 03:14:29.020565  4576 funcs.py:49] ====================
I0621 03:14:29.021562  4576 funcs.py:50] EPISODE 1 OF 30
I0621 03:14:29.022559  4576 funcs.py:51] ====================
I0621 03:14:29.024565  4576 funcs.py:71] best_player plays as X
I0621 03:14:29.025551  4576 game.py:227] ['-', '-', '-', '-', '-', '-', '-']
I0621 03:14:29.026549  4576 game.py:227] ['-', '-', '-', '-', '-', '-', '-']
I0621 03:14:29.026549  4576 game.py:227] ['-', '-', '-', '-', '-', '-', '-']
I0621 03:14:29.027557  4576 game.py:227] ['-', '-', '-', '-', '-', '-', '-']
I0621 03:14:29.028544  4576 game.py:227] ['-', 



ITERATION NUMBER 1
BEST PLAYER VERSION 0
SELF PLAYING 30 EPISODES...
1 

I0621 03:14:29.840374  4576 agent.py:137] PREDICTED VALUE FOR 1: 0.000000
I0621 03:14:29.841388  4576 agent.py:146] added node...000000000000000000000000000000000001000000000000000000000000000000000000000000000000...p = 0.142857
I0621 03:14:29.842400  4576 agent.py:146] added node...000000000000000000000000000000000000100000000000000000000000000000000000000000000000...p = 0.142857
I0621 03:14:29.843364  4576 agent.py:146] added node...000000000000000000000000000000000000010000000000000000000000000000000000000000000000...p = 0.142857
I0621 03:14:29.845366  4576 agent.py:146] added node...000000000000000000000000000000000000001000000000000000000000000000000000000000000000...p = 0.142857
I0621 03:14:29.847357  4576 agent.py:146] added node...000000000000000000000000000000000000000100000000000000000000000000000000000000000000...p = 0.142857
I0621 03:14:29.849357  4576 agent.py:146] added node...000000000000000000000000000000000000000010000000000000000000000000000000000000000000...p = 0.142

I0621 03:14:29.967036  4576 MCTS.py:94] action with highest Q + U...41
I0621 03:14:29.968031  4576 MCTS.py:100] DONE...0
I0621 03:14:29.969030  4576 game.py:227] ['-', '-', '-', '-', '-', '-', '-']
I0621 03:14:29.969030  4576 game.py:227] ['-', '-', '-', '-', '-', '-', '-']
I0621 03:14:29.970028  4576 game.py:227] ['-', '-', '-', '-', '-', '-', '-']
I0621 03:14:29.970028  4576 game.py:227] ['-', '-', '-', '-', '-', '-', '-']
I0621 03:14:29.971023  4576 game.py:227] ['-', '-', '-', '-', '-', '-', '-']
I0621 03:14:29.972023  4576 game.py:227] ['-', '-', '-', '-', '-', '-', 'X']
I0621 03:14:29.973019  4576 game.py:228] --------------
I0621 03:14:29.974017  4576 agent.py:132] ------EVALUATING LEAF------
I0621 03:14:29.980000  4576 agent.py:137] PREDICTED VALUE FOR -1: -0.029762
I0621 03:14:29.981995  4576 agent.py:146] added node...000000000000000000000000000000000000000001000000000000000000000000000000000010000000...p = 0.147818
I0621 03:14:29.982991  4576 agent.py:146] added node...00000

I0621 03:14:30.051809  4576 agent.py:61] CURRENT PLAYER...1
I0621 03:14:30.052805  4576 MCTS.py:52] ------MOVING TO LEAF------
I0621 03:14:30.053803  4576 MCTS.py:62] PLAYER TURN...1
I0621 03:14:30.055797  4576 MCTS.py:87] action: 35 (0)... N = 1, P = 0.142857, nu = 0.172884, adjP = 0.148863, W = 0.030630, Q = 0.030630, U = 0.128919, Q+U = 0.159549
I0621 03:14:30.056795  4576 MCTS.py:87] action: 36 (1)... N = 0, P = 0.142857, nu = 0.019121, adjP = 0.118110, W = 0.000000, Q = 0.000000, U = 0.204572, Q+U = 0.204572
I0621 03:14:30.057792  4576 MCTS.py:87] action: 37 (2)... N = 0, P = 0.142857, nu = 0.092098, adjP = 0.132705, W = 0.000000, Q = 0.000000, U = 0.229852, Q+U = 0.229852
I0621 03:14:30.058808  4576 MCTS.py:87] action: 38 (3)... N = 0, P = 0.142857, nu = 0.107198, adjP = 0.135725, W = 0.000000, Q = 0.000000, U = 0.235083, Q+U = 0.235083
I0621 03:14:30.059787  4576 MCTS.py:87] action: 39 (4)... N = 0, P = 0.142857, nu = 0.043724, adjP = 0.123030, W = 0.000000, Q = 0.000000, U = 0.

...

I0621 03:15:31.108537  4576 game.py:227] ['-', '-', '-', '-', '-', '-', '-']
I0621 03:15:31.110532  4576 game.py:227] ['-', '-', '-', 'O', '-', '-', '-']
I0621 03:15:31.111530  4576 game.py:227] ['-', '-', '-', 'X', '-', 'O', '-']
I0621 03:15:31.112527  4576 game.py:227] ['-', '-', 'X', 'O', '-', 'O', '-']
I0621 03:15:31.113524  4576 game.py:227] ['-', '-', 'X', 'X', '-', 'O', 'X']
I0621 03:15:31.114522  4576 game.py:228] --------------
I0621 03:15:31.115519  4576 agent.py:83] ***************************
I0621 03:15:31.116516  4576 agent.py:84] ****** SIMULATION 38 ******
I0621 03:15:31.117513  4576 agent.py:85] ***************************
I0621 03:15:31.118511  4576 agent.py:59] ROOT NODE...000000000000000000000000100000000000011001000000000000000000000000000000010100000010
I0621 03:15:31.119508  4576 game.py:227] ['-', '-', '-', '-', '-', '-', '-']
I0621 03:15:31.120516  4576 game.py:227] ['-', '-', '-', '-', '-', '-', '-']
I0621 03:15:31.121503  4576 game.py:227] ['-', '-', '-', '-'

I0621 03:15:31.209268  4576 MCTS.py:87] action: 17 (3)... N = 6, P = 0.149294, nu = 0.167142, adjP = 0.152864, W = -0.180443, Q = -0.030074, U = 0.146491, Q+U = 0.116418
I0621 03:15:31.209268  4576 MCTS.py:87] action: 26 (5)... N = 7, P = 0.129374, nu = 0.119021, adjP = 0.127303, W = 0.214023, Q = 0.030575, U = 0.106747, Q+U = 0.137322
I0621 03:15:31.210266  4576 MCTS.py:87] action: 30 (2)... N = 7, P = 0.174596, nu = 0.218161, adjP = 0.183309, W = 0.156091, Q = 0.022299, U = 0.153709, Q+U = 0.176008
I0621 03:15:31.212259  4576 MCTS.py:87] action: 34 (6)... N = 7, P = 0.135588, nu = 0.126200, adjP = 0.133710, W = 0.037454, Q = 0.005351, U = 0.112119, Q+U = 0.117470
I0621 03:15:31.213258  4576 MCTS.py:87] action: 35 (0)... N = 6, P = 0.123183, nu = 0.030568, adjP = 0.104660, W = -0.138074, Q = -0.023012, U = 0.100297, Q+U = 0.077285
I0621 03:15:31.215253  4576 MCTS.py:87] action: 36 (1)... N = 6, P = 0.146044, nu = 0.318091, adjP = 0.180454, W = -0.067438, Q = -0.011240, U = 0.172931, Q

I0621 03:15:31.302019  4576 MCTS.py:87] action: 26 (5)... N = 2, P = 0.156395, nu = 0.000000, adjP = 0.156395, W = 0.061194, Q = 0.030597, U = 0.116570, Q+U = 0.147167
I0621 03:15:31.304014  4576 MCTS.py:87] action: 29 (1)... N = 0, P = 0.132350, nu = 0.000000, adjP = 0.132350, W = 0.000000, Q = 0.000000, U = 0.295943, Q+U = 0.295943
I0621 03:15:31.305012  4576 MCTS.py:87] action: 30 (2)... N = 0, P = 0.146329, nu = 0.000000, adjP = 0.146329, W = 0.000000, Q = 0.000000, U = 0.327202, Q+U = 0.327202
I0621 03:15:31.306009  4576 MCTS.py:87] action: 34 (6)... N = 0, P = 0.147630, nu = 0.000000, adjP = 0.147630, W = 0.000000, Q = 0.000000, U = 0.330111, Q+U = 0.330111
I0621 03:15:31.307007  4576 MCTS.py:87] action: 35 (0)... N = 0, P = 0.116264, nu = 0.000000, adjP = 0.116264, W = 0.000000, Q = 0.000000, U = 0.259975, Q+U = 0.259975
I0621 03:15:31.308004  4576 MCTS.py:87] action: 39 (4)... N = 1, P = 0.152266, nu = 0.000000, adjP = 0.152266, W = 0.218849, Q = 0.218849, U = 0.170238, Q+U = 0

I0621 03:15:31.382805  4576 MCTS.py:87] action: 39 (4)... N = 6, P = 0.141921, nu = 0.150317, adjP = 0.143600, W = -0.158951, Q = -0.026492, U = 0.140639, Q+U = 0.114147
I0621 03:15:31.382805  4576 MCTS.py:94] action with highest Q + U...34
I0621 03:15:31.383813  4576 MCTS.py:62] PLAYER TURN...1
I0621 03:15:31.384800  4576 MCTS.py:87] action: 17 (3)... N = 2, P = 0.145442, nu = 0.000000, adjP = 0.145442, W = -0.018501, Q = -0.009251, U = 0.118753, Q+U = 0.109502
I0621 03:15:31.385797  4576 MCTS.py:87] action: 26 (5)... N = 1, P = 0.156652, nu = 0.000000, adjP = 0.156652, W = 0.192706, Q = 0.192706, U = 0.191859, Q+U = 0.384565
I0621 03:15:31.385797  4576 MCTS.py:87] action: 27 (6)... N = 0, P = 0.114128, nu = 0.000000, adjP = 0.114128, W = 0.000000, Q = 0.000000, U = 0.279555, Q+U = 0.279555
I0621 03:15:31.386794  4576 MCTS.py:87] action: 30 (2)... N = 2, P = 0.157352, nu = 0.000000, adjP = 0.157352, W = 0.106753, Q = 0.053377, U = 0.128478, Q+U = 0.181854
I0621 03:15:31.387791  4576 M

KeyboardInterrupt: 

## The following panels are not involved in the learning process

### Play matches between versions (use -1 for human player)

In [4]:
from game import Game
from funcs import playMatchesBetweenVersions
import loggers as lg

env = Game()
playMatchesBetweenVersions(env, 1, 1, 1, 10, lg.logger_tourney, 0)

OSError: Unable to open file (unable to open file: name = './run_archive/connect4/run0001/models/version0001.h5', errno = 2, error message = 'No such file or directory', flags = 0, o_flags = 0)

### Pass a particular game state through the neural network (setup below for Connect4)

In [ ]:
gs = GameState(np.array([
    0,0,0,0,0,0,0,
    0,0,0,0,0,0,0,
    0,0,0,0,0,0,0,
    0,0,0,0,0,0,0,
    0,0,0,0,0,0,0,
    0,0,0,0,0,0,0
]), 1)

preds = current_player.get_preds(gs)

print(preds)

### See the layers of the current neural network

In [ ]:
current_player.model.viewLayers()

### Output a diagram of the neural network architecture

In [ ]:
from keras.utils import plot_model
plot_model(current_NN.model, to_file=run_folder + 'models/model.png', show_shapes = True)